In [1]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.datasets import load_digits
from sklearn.feature_selection import SelectKBest, chi2
from sklearn.model_selection import KFold
from sklearn.model_selection import train_test_split
from sklearn.dummy import DummyClassifier
import re
from data_cleaning import *

# 1. Preprocessing

In [2]:
# read data
train_data = pd.read_csv("Train.csv", sep=',')
test_data = pd.read_csv("Test.csv", sep=',')

In [3]:
#separating instance and label for Train
X_train_raw = [x[0] for x in train_data[['text']].values]
Y_train = [x[0] for x in train_data[['sentiment']].values]
X_test_raw = [x[0] for x in test_data[['text']].values]

#### (1). data cleaning

In [4]:
# 1. data cleaning (optional)
X_train_need_to_clean = pd.DataFrame(X_train_raw)
X_test_need_to_clean = pd.DataFrame(X_test_raw)

# remove url, # and @
X_train_need_to_clean.replace("\b*https?:\S*", '', regex=True, inplace=True)
X_train_need_to_clean.replace("\b*@\S*", '', regex=True, inplace=True)
X_train_need_to_clean.replace("\b*#\S*", '', regex=True, inplace=True)
X_test_need_to_clean.replace("\b*https?:\S*", '', regex=True, inplace=True)
X_test_need_to_clean.replace("\b*@\S*", '', regex=True, inplace=True)
X_test_need_to_clean.replace("\b*#\S*", '', regex=True, inplace=True)

for i in range(X_train_need_to_clean.shape[0]):
    X_train_need_to_clean.loc[i, 0] = ' '.join(text_preprocessing(X_train_need_to_clean.loc[i, 0], remove_html=False))

X_train_clean = [x[0] for x in X_train_need_to_clean[[0]].values]
X_test_clean = [x[0] for x in X_test_need_to_clean[[0]].values]

In [12]:
pd.set_option("display.max_rows",None)
pd.set_option("display.max_columns",None)
X_train_need_to_clean

0
0      doctor hit campaign trail race medical council...
1      anybody go radio station tomorrow shawn friend...
2                             find naruto not 5th hokage
3      prince george reservist die saturday want help...
4        season sun versi nirvana rancak gak slow rockkk
5                                      not sun lady gaga
6                                                   cute
7      today international day elimination violence w...
8      game april david wright go for-5 hr bb r monda...
9                    josh hamilton fly center go 9th tie
10           watch trump protest shut part new york city
11     want basse try dark soul vid dark souls ii gia...
12          hour shift consist think ed sheeran tomorrow
13               seriously debate go paper town tomorrow
14        pay back senior citizen medicare service shame
15     stop post picture january charlie hebdo attack...
16                 david price toronto blue jays offense
17     buy scuba suit underwater scene sharknado tomo...
18                               kanye west carry speech
19      export british value liberty democracy look like
20                good description maduro pin head thank
21              new || niall you.s open today today sept
22                                      cover homeopathy
23     assad troop take percent rebel hold aleppo rus...
24                                        death death no
25     not go not true muslim criminal not mean islam...
26                 hi guy new iron maiden vinyl tomorrow
27     directly address american people info website ...
28     year leave planet sun ra premiere tone poem ' ...
29     fun friday mashup ---&gt nelly hot mash bee ge...
30                   rally beath white sox tuesday night
31     teen kid say old dude paul mccartney chance mu...
32      officially pga week dustin johnson 2nd time pick
33                                              donate |
34     happy birthday dude jason aldean bout live com...
35     end problem laundering & currency conversion p...
36                     luke2 emily gilmore3 sukie4 paris
37                           go fabrique milan italy apr
38     u2 concert park long week chillin family 10th ...
39        fact listen zac brown band gloomy day sun come
40     happy friday national hot dog day not mean not...
41     ivanka play flotus --pres.-elect drumpf ivanka...
42                tim duncan play season able savage uoi
43          nakita akong 5sos vamps shirt want want want
44     scotland v germany tonight foo fighter tomorro...
45     reason know john cena bully 3rd grade write sh...
46                  picture january charlie hebdo attack
47     tristan mcdaniel score yard milan lead humbold...
48                                      wait maduro turn
49     tor beat min david price debut jay tie 2nd wil...
50      win golf tournament 1st day dustin johnson major
51      undertaker go tombstone shit brock lesnar sunday
52     persuasive speech depression pro con death pen...
53        saturday day hour minute second ed sheeran atl
54     cheeto nazi mad fat ass look like tub curdle o...
55     research paper minimum wage literally write su...
56                     focus step step implement program
57     vid hide valuable inside hollow decorative candle
58     hillary clinton caitlyn jenner nobel peace pri...
59     crazy thing deep learning topological datum an...
60     idea write christian god totally not willingto...
61                    fuckin kendrick lamar black friday
62                         wwe monday raw goat john cena
63     hard year addition lose leonard cohen david bo...
64     sushi coworker apparently go la 24th stick cov...
65           ff fall asleep open position murray 4th set
66     10th hole good birdie hole dustin johnson bird...
67     think frank ocean release november music great...
68     riverside yoga race street pier awesome way st...
69                reporter visit islamic state terrirory
70      

#### (2). vectorization (transformation)

In [6]:


# bag of words
# countvectorizer
BoW_vectorizer = CountVectorizer(analyzer='word', ngram_range=(2,2))
X_train_BoW = BoW_vectorizer.fit_transform(X_train_clean)
X_test_BoW = BoW_vectorizer.transform(X_test_clean)

In [7]:
# 3. feature selection
X_train_new = SelectKBest(chi2,k=5000).fit_transform(X_train_BoW,Y_train)


In [8]:
# 4. split
train_size = X_train_BoW.shape[0]
test_size = X_test_BoW.shape[0]
## random hold out
ts = test_size/train_size
X_train_s, X_test_s, y_train_s, y_test_s = train_test_split(X_train_new,Y_train, test_size=ts)

# modelling

## base model: 0R

In [9]:
clf = DummyClassifier(strategy='most_frequent')
basemodel = clf.fit(X_train_raw, Y_train)
print("base model score: ", basemodel.score(X_train_raw, Y_train))

base model score:  0.5806348041464086


In [10]:
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_val_score
import numpy as np
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV

## logistic regression

### choose of hyperparameter

In [11]:
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_val_score
import numpy as np
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV

hyper = {
    'solver': ['newton-cg', 'lbfgs', 'sag', 'saga'],
    'penalty': ['l1', 'l2', 'none', 'elasticnet'],
    'C': [1e-4, 1e-3, 1e-2, 1e-1, 1, 10, 100, 1000],
    'max_iter': [100, 200, 300],
    'multi_class': ['auto', 'ovr', 'multinomial']
}

##### randomised method (less computation)

In [16]:
search_logi = RandomizedSearchCV(LogisticRegression(),hyper, scoring='accuracy', cv=5, n_iter=5)

##### grid search

In [ ]:
search_logi = GridSearchCV(LogisticRegression(),hyper, scoring='accuracy', cv=5)

##### evaluation

In [17]:
logi_result = search_logi.fit(X_train_s, y_train_s)

D:\Users\laizh\anaconda3\lib\site-packages\sklearn\linear_model\_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
D:\Users\laizh\anaconda3\lib\site-packages\sklearn\linear_model\_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
D:\Users\laizh\anaconda3\lib\site-packages\sklearn\linear_model\_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
D:\Users\laizh\anaconda3\lib\site-packages\sklearn\linear_model\_sag.py:328: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn("The max_iter was reached which means "
D:\Users\laizh\anaconda3\lib\site-packages\sklearn\linear_model\_sag.py:328: ConvergenceWarning: The max_iter was reached which mean

D:\Users\laizh\anaconda3\lib\site-packages\sklearn\linear_model\_logistic.py:763: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


In [18]:
pd.DataFrame(logi_result.cv_results_)
logi_result.best_params_
logi_result.best_score_

0.6752853263900296

In [22]:
logi_result.best_params_['solver']

'lbfgs'

### SVM

In [ ]:
from sklearn.svm import SVC

print(f"svm model score: ", svm_model.score(X_test_s,y_test_s))
svm_hyper = {
    'degree': [3, 5, 10, 15],
    'gamma': [1,0.1,0.01,0.001],
    'C': [1e-5, 1e-4, 1e-3, 1e-2, 1e-1, 1, 10, 100, 1000],
    'kernel': ['linear', 'poly', 'rbf', 'sigmod'],
    'max_iter': [-1, 100, 500, 1000],
    'decision_function_shape': ['ovo', 'ovr']
}

In [ ]:
# random method
search_svm = RandomizedSearchCV(SVC(), svm_hyper, scoring='accuracy', cv=5, n_iter=100)

In [ ]:
# grid method
search_svm = GridSearchCV(SVC(), svm_hyper, scoring='accuracy', cv=5)

In [ ]:
svm_result = search_svm.fit(X_train_s, y_train_s)
pd.DataFrame(svm_result.cv_results_)
svm_result.best_params_
svm_result.best_score_

### Random Forest

In [12]:
from sklearn.ensemble import RandomForestClassifier

rf_hyper = {
    'n_estimators': [90, 100, 115 , 130],
    'criterion': ['gini', 'entropy'],
    'max_depth': range(2,20,1),
    'min_sample_leaf': range(1,10,1),
    'min_samples_split': range(2,10,1),
    'max_features': ['auto', 'log2']
}

In [ ]:
# random method
search_svm = RandomizedSearchCV(RandomForestClassifier(), rf_hyper, scoring='accuracy', cv=5, n_iter=100)

In [ ]:
# grid method 
search_svm = GridSearchCV(RandomForestClassifier(), rf_hyper, scoring='accuracy', cv=5)

In [ ]:
rf_result = search_svm.fit(X_train_s, y_train_s)
pd.DataFrame(rf_result.cv_results_)
rf_result.best_params_
rf_result.best_score_

### Stacking

In [ ]:
from sklearn.ensemble import StackingClassifier
from sklearn.tree import DecisionTreeClassifier

rf_model = RandomForestClassifier(criterion=rf_result.best_params_['criterion'], max_depth=rf_result.best_params_['max_depth'],
                                  max_features='log2', min_samples_leaf=rf_result.best_params_['min_sample_leaf'], 
                                  min_samples_split=rf_result.best_params_['min_samples_split'], n_estimators=rf_result.best_params_['n_estimators'],
                                  random_state=0).fit(X_train_s, y_train_s)

svm_model = SVC(degree=svm_result.best_params_['degree'], gamma=svm_result.best_params_['gamma'] ,C=svm_result.best_params_['C'], 
                kernel=svm_result.best_params_['kernel'], max_iter=svm_result.best_params_['max_iter'], 
                decision_function_shape=svm_result.best_params_['decision_function_shape']).fit(X_train_s, y_train_s)

logi_model = LogisticRegression(solver=logi_result.best_params_['solver'], penalty=logi_result.best_params_['penalty'],
                                C=logi_result.best_params_['C'], max_iter=logi_result.best_params_['max_iter'],
                                multi_class=logi_result.best_params_['multi_class']).fit(X_train_s, y_train_s)

estimators = [('rf', rf_model),('svr', svm_model), ('log', logi_model)]

In [ ]:
dt_stacking = StackingClassifier(estimator=estimators, final_estimator=DecisionTreeClassifier())

In [ ]:
svm_stacking = StackingClassifier(estimator=estimators, final_estimator=SVC())